In [1]:
import pandas as pd
import numpy as np
import scipy.stats as sp
import scipy.optimize as sco
import plotly
from plotly import graph_objs as go
from plotly.subplots import make_subplots
plotly.offline.init_notebook_mode(connected = True)

In [2]:
def BSM(S0, K, tau, r, sigma, opt_type='c', q=0):
    d1 = (np.log(S0/K)+(r-q+.5*sigma**2)*tau)/(sigma*np.sqrt(tau))
    d2 = d1 - sigma*np.sqrt(tau)
    N = lambda x: sp.norm.cdf(x)
    if opt_type == 'c':
        return S0*np.exp(-q*tau)*N(d1) - np.exp(-r*tau)*K*N(d2)
    else:
        return K*np.exp(-r*tau)*N(-d2) - S0*np.exp(-q*tau)*N(-d1)

In [3]:
files = ['20180427', '20180504', '20180511', '20180518', '20180525', '20180601', '20180608', '20180615',
        '20180720', '20180817', '20180921', '20181019', '20181116', '20190118', '20190215', '20190621',
        '20200117']
r = 0.0184 # 3m Treasury 4/30/18
dfs = []
for f in files:
    temp = pd.read_csv('{}.csv'.format(f))
    temp['TTM'] = (pd.to_datetime(temp['T'].apply(lambda x: str(x))) - pd.datetime(2018,4,27)).apply(lambda x: x.days)/365
    dfs.append(temp)
S = dfs[0].S[0]
dfs[0].TTM = 1/365
dfs

[     Unnamed: 0         T       K   P_bid   P_ask   C_bid   C_ask        S  \
 0             0  20180427   910.0    0.00    0.02  607.10  611.80  1517.96   
 1             1  20180427   920.0    0.00    0.03  596.50  601.50  1517.96   
 2             2  20180427   930.0    0.00    3.80  586.70  591.70  1517.96   
 3             3  20180427   940.0    0.00    0.05  576.50  581.50  1517.96   
 4             4  20180427   950.0    0.00    0.05  566.50  571.50  1517.96   
 5             5  20180427   960.0    0.00    1.67  556.40  561.40  1517.96   
 6             6  20180427   970.0    0.00    3.35  546.50  551.50  1517.96   
 7             7  20180427   980.0    0.00    4.25  536.50  541.50  1517.96   
 8             8  20180427   990.0    0.00    0.68  526.55  531.55  1517.96   
 9             9  20180427  1000.0    0.00    0.04  516.55  521.55  1517.96   
 10           10  20180427  1010.0    0.00    0.68  506.55  511.55  1517.96   
 11           11  20180427  1020.0    0.00    0.08  

In [4]:
tol = 10E-9
def SVI(df,a,b,p,m,sig):
    k = np.log(np.asarray(df.K)/1517.96)
    return a + b*(p*(np.asarray(k)-m) + np.sqrt((np.asarray(k)-m)**2 + sig**2))

def SVI_fit(df,IV_col):
    obj = lambda x: np.sum((SVI(df, x[0], x[1], x[2], x[3], x[4]) - np.asarray(df[IV_col]))**2)
    cons = ({'type':'ineq','fun': lambda x: x[0] + x[1]*x[4]*np.sqrt(1 - x[2]**2)},
            {'type':'ineq','fun': lambda x: x[1]},
            {'type':'ineq','fun': lambda x: x[4] - tol})
    bnds = ((None,None),(0,None),(-1+tol,1-tol),(None,None),(tol,None))
    guess = [.01,.01,.01,.01,.01]
    result = sco.minimize(obj,guess,constraints=cons,bounds=bnds,tol=tol)
    return result

SVI_fit(dfs[0],'Comb_vol')

     fun: 1.6554086383917688
     jac: array([-0.00085485, -0.00035636,  0.00061601,  0.0002605 , -0.00642359])
 message: 'Optimization terminated successfully.'
    nfev: 371
     nit: 49
    njev: 49
  status: 0
 success: True
       x: array([-2.19721984, 11.73399722,  0.11266262,  0.04544888,  0.28812271])

In [5]:
def cs(x,y):
    n = len(y)
    R_vec = np.append(np.array(y),np.array((0,0)))
    t = np.array(x)
    A = np.zeros((n+2,n+2))
    plus = lambda x: max(x,0)
    t1 = t[0]
    for i in range(n):
        c2 = t[i] - t1
        A[i,] = [1, c2, c2**2] + [plus(t[i] - t[j])**3 for j in range(n-1)]
    A[n,] = [0,0,2] + [0]*(n-1)
    A[n+1,] = [0,0,2] + [6*plus(t[n-1] - t[k]) for k in range(n-1)]
    return np.dot(np.linalg.inv(A),R_vec)

def interpolate(t_int, x, y):
    n = len(t_int)
    coef = cs(x,y)
    plus = lambda x: max(x,0)
    y_int = np.zeros(n)
    for i in range(n):
        temp = t_int[i] - x[0]
        y_int[i] = \
        sum([coef[0],coef[1]*temp,coef[2]*temp**2]+[coef[j+3]*plus(t_int[i]-x[j])**3 for j in range(len(coef)-3)])
    return y_int

In [7]:
CS_dfs = []
ind_delta = [50,50,35,50,35,20,5,50,20,25,25,25,25,25,25,25,25]
for i in range(len(dfs)):
    temp = dfs[i]

    fit1 = SVI_fit(temp[temp.K < S],'Comb_vol')['x']
    fit2 = SVI_fit(temp[temp.K > S],'Comb_vol')['x']

    temp['SVI'] = np.append(SVI(temp[temp.K < S],fit1[0],fit1[1],fit1[2],fit1[3],fit1[4]),
              SVI(temp[temp.K > S],fit2[0],fit2[1],fit2[2],fit2[3],fit2[4]), axis=0)
    
    dfs[i]['SVI'] = temp.SVI

    temp2 = temp[temp.index.isin(np.append(np.arange(0,len(temp),ind_delta[i]),
                                           max(temp.index)))].reset_index(drop=True)
    start = int(min(temp.K)-100)
    end = int(max(temp.K)+100)
    t_int = np.linspace(start,end,(end-start)*4+1)
    y_int = interpolate(t_int, temp2.K, temp2['SVI'])

    temp3 = pd.DataFrame({'K': t_int, 'TTM': dfs[i].TTM[0], 'Sigma': y_int})
    temp3['SVI'] = np.append(SVI(temp3[temp3.K < S],fit1[0],fit1[1],fit1[2],fit1[3],fit1[4]),
              SVI(temp3[temp3.K > S],fit2[0],fit2[1],fit2[2],fit2[3],fit2[4]), axis=0)
    temp3['C'] = temp3.apply(lambda x: BSM(S,x.K,x.TTM,r,x.Sigma), axis=1)
    temp3['C_SVI'] = temp3.apply(lambda x: BSM(S,x.K,x.TTM,r,x.SVI), axis=1)
    temp3['PDF'] = (temp3.C.shift(-1) - 2*temp3.C + temp3.C.shift(1))/(.25**2)
    temp3['PDF_SVI'] = (temp3.C_SVI.shift(-1) - 2*temp3.C_SVI + temp3.C_SVI.shift(1))/(.25**2)
    temp3.dropna(inplace=True)
    temp3['PDF'] = temp3.PDF/temp3.PDF.sum()
    temp3['PDF_SVI'] = temp3.PDF_SVI/temp3.PDF_SVI.sum()
    CS_dfs.append(temp3)

In [16]:
# temp[(temp.K > 1515) & (temp.K < 1519)]
temp[(temp.K < 1517.75) | (temp.K > 1518)]

K      TTM     Sigma       SVI           C       C_SVI  \
1      810.25  0.00274  5.066991  5.219555  708.627316  708.858209   
2      810.50  0.00274  5.065126  5.217172  708.377910  708.608153   
3      810.75  0.00274  5.063261  5.214789  708.128504  708.358097   
4      811.00  0.00274  5.061396  5.212406  707.879098  708.108041   
5      811.25  0.00274  5.059531  5.210025  707.629691  707.857985   
6      811.50  0.00274  5.057666  5.207644  707.380284  707.607929   
7      811.75  0.00274  5.055801  5.205264  707.130877  707.357873   
8      812.00  0.00274  5.053935  5.202885  706.881470  707.107817   
9      812.25  0.00274  5.052070  5.200506  706.632063  706.857761   
10     812.50  0.00274  5.050205  5.198129  706.382655  706.607705   
11     812.75  0.00274  5.048340  5.195752  706.133247  706.357649   
12     813.00  0.00274  5.046475  5.193375  705.883839  706.107594   
13     813.25  0.00274  5.044610  5.191000  705.634431  705.857538   
14     813.50  0.00274  5.042745  5.188625  705.385022  705.607482   
15     813.75  0.00274  5.040880  5.186251  705.135614  705.357426   
16     814.00  0.00274  5.039015  5.183877  704.886205  705.107370   
17     814.25  0.00274  5.037150  5.181505  704.636796  704.857315   
18     814.50  0.00274  5.035285  5.179133  704.387386  704.607259   
19     814.75  0.00274  5.033420  5.176762  704.137976  704.357203   
20     815.00  0.00274  5.031555  5.174391  703.888566  704.107148   
21     815.25  0.00274  5.029690  5.172022  703.639156  703.857092   
22     815.50  0.00274  5.027824  5.169653  703.389746  703.607037   
23     815.75  0.00274  5.025959  5.167284  703.140335  703.356981   
24     816.00  0.00274  5.024094  5.164917  702.890925  703.106926   
25     816.25  0.00274  5.022229  5.162550  702.641514  702.856870   
26     816.50  0.00274  5.020364  5.160184  702.392102  702.606815   
27     816.75  0.00274  5.018499  5.157819  702.142691  702.356759   
28     817.00  0.00274  5.016634  5.155454  701.893279  702.106704   
29     817.25  0.00274  5.014769  5.153090  701.643867  701.856649   
30     817.50  0.00274  5.012904  5.150727  701.394455  701.606593   
...       ...      ...       ...       ...         ...         ...   
5690  2232.50  0.00274  3.313174  3.298896    1.451905    1.406299   
5691  2232.75  0.00274  3.314123  3.299755    1.452363    1.406472   
5692  2233.00  0.00274  3.315072  3.300614    1.452822    1.406644   
5693  2233.25  0.00274  3.316021  3.301472    1.453282    1.406817   
5694  2233.50  0.00274  3.316970  3.302331    1.453744    1.406989   
5695  2233.75  0.00274  3.317920  3.303190    1.454206    1.407162   
5696  2234.00  0.00274  3.318870  3.304048    1.454670    1.407335   
5697  2234.25  0.00274  3.319821  3.304906    1.455135    1.407507   
5698  2234.50  0.00274  3.320771  3.305765    1.455602    1.407680   
5699  2234.75  0.00274  3.321722  3.306623    1.456069    1.407853   
5700  2235.00  0.00274  3.322673  3.307481    1.456538    1.408026   
5701  2235.25  0.00274  3.323625  3.308339    1.457008    1.408199   
5702  2235.50  0.00274  3.324577  3.309197    1.457480    1.408372   
5703  2235.75  0.00274  3.325529  3.310055    1.457952    1.408545   
5704  2236.00  0.00274  3.326481  3.310913    1.458426    1.408718   
5705  2236.25  0.00274  3.327434  3.311770    1.458901    1.408891   
5706  2236.50  0.00274  3.328386  3.312628    1.459378    1.409064   
5707  2236.75  0.00274  3.329340  3.313485    1.459856    1.409238   
5708  2237.00  0.00274  3.330293  3.314343    1.460335    1.409411   
5709  2237.25  0.00274  3.331247  3.315200    1.460815    1.409585   
5710  2237.50  0.00274  3.332201  3.316057    1.461296    1.409758   
5711  2237.75  0.00274  3.333155  3.316914    1.461779    1.409932   
5712  2238.00  0.00274  3.334110  3.317771    1.462263    1.410105   
5713  2238.25  0.00274  3.335065  3.318628    1.462748    1.410279   
5714  2238.50  0.00274  3.336020  3.319485    1.463235    1.410453   
5715  2238.75  0.00274

In [22]:
temp = CS_dfs[0]
trace0 = go.Scatter(
    x = temp.K, y = temp.PDF, name = 'CS PDF'
)
trace1 = go.Scatter(
    x = temp[(temp.K < 1517.75) | (temp.K > 1518)].K, y = temp[(temp.K < 1517.75) | (temp.K > 1518)].PDF_SVI, 
    name = 'SVI PDF'
)
trace2 = go.Scatter(x = 10*[1572.62], y = np.linspace(0,0.0012,10), name = 'AMZN Close', mode='lines',
                   line = dict(dash='dash'))
trace3 = go.Scatter(x = 10*[S], y = np.linspace(0,0.0012,10), name = 'ATM', mode='lines',
                   line = dict(dash='dash'))
data = [trace1, trace0, trace2, trace3]
layout = go.Layout(title = 'AMZN SVI and Cubic Spline PDFs {}'.format(dfs[0]['T'][0]), 
                   yaxis = dict(title = 'Probability Density'), xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)

In [7]:
pd.DataFrame(
    {'Length': [len(df) for df in dfs[:i+1]],
     'CS Points':[len(temp[temp.index.isin(np.arange(0,len(temp),ind))])+1 for temp,ind in zip(dfs[:i+1],ind_delta)],
    'Delta': ind_delta}
).T

0    1    2    3    4    5   6    7    8    9    10   11   12  \
Length     304  306  179  251  180  148  29  211  151  128  116  111  137   
CS Points    8    8    7    7    7    9   7    6    9    7    6    6    7   
Delta       50   50   35   50   35   20   5   50   20   25   25   25   25   

            13   14   15   16  
Length     161  137  124  132  
CS Points    8    7    6    7  
Delta       25   25   25   25

In [43]:
CS_dfs[0].head()

K      TTM     Sigma           C           PDF
1  810.25  0.00274  5.066991  708.627316 -8.663874e-07
2  810.50  0.00274  5.065126  708.377910 -8.693749e-07
3  810.75  0.00274  5.063261  708.128504 -8.723610e-07
4  811.00  0.00274  5.061396  707.879098 -8.753481e-07
5  811.25  0.00274  5.059531  707.629691 -8.783379e-07

In [81]:
sum_table = pd.DataFrame(
    {'Maturity': [pd.to_datetime(dfs[i]['T'].apply(lambda x: str(x)))[0] 
                  for i in list(range(6)) + list(range(7,len(CS_dfs)))],
    'E[S]': [sum(np.array(CS_dfs[i].PDF)*np.array(CS_dfs[i].K)) 
             for i in list(range(6)) + list(range(7,len(CS_dfs)))]})
# sum_table.set_index('Maturity',inplace=True)

sum_table = pd.merge(sum_table.iloc[:8], sum_table.iloc[8:].reset_index(drop=True), 
                     left_index=True, right_index=True)
sum_table.columns = ['Maturity', 'E[S]', 'Maturity', 'E[S]']
sum_table

Maturity         E[S]   Maturity         E[S]
0 2018-04-27  1520.522454 2018-08-17  1528.012168
1 2018-05-04  1521.228683 2018-09-21  1532.040556
2 2018-05-11  1522.747693 2018-10-19  1530.365743
3 2018-05-18  1527.978573 2018-11-16  1529.376044
4 2018-05-25  1525.219392 2019-01-18  1542.005351
5 2018-06-01  1521.301758 2019-02-15  1513.123232
6 2018-06-15  1533.139335 2019-06-21  1528.309534
7 2018-07-20  1535.757050 2020-01-17  1527.983312

In [80]:
sum_table[sum_table['E[S]'] > S].mean()

E[S]    1528.399176
dtype: float64

In [29]:
S

1517.96

In [42]:
(1527.4444298160847-S)/S

0.006248142122377853

In [56]:
(1528.399176-S)/S

0.00687710875121865

In [88]:
trace2 = go.Scatter(x = 10*[1572.62], y = np.linspace(0,0.0011,10), name = 'Underlying', mode='lines')
data = [trace2]
for i in list(range(6)) + list(range(7,14)) + list(range(15,len(CS_dfs)-1)):
    trace = go.Scatter(x = CS_dfs[i].K, y = CS_dfs[i].PDF, name = 'f(S) {}'.format(files[i]))
    data.append(trace)
layout = go.Layout(title = 'AMZN PDF', yaxis = dict(title = 'Probability Density'),
                   xaxis = dict(title = 'S'))
fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig)